In [5]:
#header files
import pandas as pd
import timeit
from copy import deepcopy
import multiprocessing
import os
import json
from sklearn.model_selection import KFold

In [14]:
#reading the file

start = timeit.default_timer()   # to note time
filename = "Brown_tagged_train.txt"

print("Reading the file..........\n")
f = open(filename, "r")
maintxt = f.read()
sentences = list(map(str,maintxt.split("\n")))
for i in range(len(sentences)-1,-1,-1):
    if len(sentences[i])< 2:
        sentences.pop(i)

Reading the file..........



In [15]:
#3 functions

def breakWordTag(s):
    if s.find("/") > 0:
        l  = s.split("/")
        return " ".join(l[:-1]) , l[-1]
    return None,None

# def formVocabDict(wor):          
#     if wor in vocab:
#         vocab[wor] += 1
#     else:
#         vocab[wor] = 1
def formRequiredTextTaggedList(orig_text,orig_tagged,indices):
    temp_text_list = []
    temp_tagged_list = []
    for index in indices:
        temp_text_list.append(orig_text[index])
        temp_tagged_list.append(orig_tagged[index])
    return temp_text_list, temp_tagged_list


# def updateTagAndWordDict(word,tag):
#     if tag in tag_dict:
#         if word in tag_dict[tag]:
#             tag_dict[tag][word] += 1
#         else:
#             tag_dict[tag][word] = 1
#         tag_count[tag] += 1
#         formVocabDict(word)
#     else:
#         tag_dict[tag] = {word:1}
#         tag_count[tag] = 1

def formTransitionMatrix(tag_count,tagged_sent):    
    transition_matrix = {"ST1":{}}     #transition matrix
    for i in tag_count:
        transition_matrix[i] = {}

    for i in transition_matrix:
        for j in tag_count:
            transition_matrix[i][j] = 0
        transition_matrix[i]["END1"] = 0

    for tag_sent in tagged_sent:
        transition_matrix["ST1"][tag_sent[0]] += 1
        for j in range(1,len(tag_sent)):
            transition_matrix[tag_sent[j-1]][tag_sent[j]] += 1
        transition_matrix[tag_sent[-1]]["END1"] += 1

    for i in transition_matrix:
        for j in transition_matrix[i]:
            transition_matrix[i][j] += 1           #SMOOTHING
    for i in transition_matrix:
        coun = 0
        for j in transition_matrix[i]:
            coun += transition_matrix[i][j]
        coun = max(1,coun)
        for j in transition_matrix[i]:
            transition_matrix[i][j] /= coun
    return transition_matrix

def getEmissionProb(word,tag,tag_dict,vocab):         # to give relative emission probability
    if word not in vocab:      #SMOOTHING
        return 1
    if word in tag_dict[tag]:
        return tag_dict[tag][word]
    return 0

# def remover():
#     rem = 5                   # tune your speed lesser is higher
#     if len(removlist) > rem:
#         removlist.sort(reverse = True)
#         ele = removlist[rem]
#         for i in range(len(que2)-1,-1,-1):
#             if que2[i] < ele:
#                 que1.pop(i)
#                 que2.pop(i)
                
def precall(ke,tagwise_metric,average):
    fn = tagwise_metric[ke]["fn"]
    fp = tagwise_metric[ke]["fp"]
    tp = tagwise_metric[ke]["tp"]
    try:
        precision = tp/(tp+fp)
        recall = tp/(tp+fn)
        f1s = 2/((1/recall)+(1/precision))
        average[0].append(precision)
        average[1].append(recall)
        average[2].append(f1s)
    except:
        precision = 0
        recall = 0
        f1s = 0	

    tagwise_metric[ke]["precision"] = precision
    tagwise_metric[ke]["recall"] = recall
    tagwise_metric[ke]["f1s"] = f1s
    return tagwise_metric, average

In [16]:
#defining some holders

# tag_dict = {}              # tag dictionary (Emision matrix)
# tag_count = {}             # count accurance of tags
# vocab ={}                  # vocabulary
# word_dict = {}             # word dictionary

text_sent = []             # contain list of sentencess
tagged_sent = []           # contain list of ist of tagged sentencess

testingsen = []            # contain testing sentencess
testingtag = []            # contain testing tags

senten_length = []
  

In [17]:
print("Breaking into sentencess and tags..........\n")    

for i in sentences:  
    ss = list(map(str,i.split()))       # process sentencess
    temp1 = []
    temp2 = []
    for j in ss:
        wor,tag = breakWordTag(j)
        if wor != None:
            temp1.append(wor)
            temp2.append(tag)
#             if wor not in word_dict:
#                 word_dict[wor] = {}
#             word_dict[wor][tag] = 0
    if len(temp1) > 1:                # remove lesser length sentencess
        text_sent.append(temp1)
        tagged_sent.append(temp2)
        senten_length.append(len(temp1))

orig_text_sent = text_sent
orig_tagged_sent = tagged_sent

Breaking into sentencess and tags..........



In [22]:
#perform k fold 
k = 3
n = len(orig_text_sent)
kf = KFold(n_splits=k)



foldi = 1
#accuracy, precision, recall, f1 score
total_metric = [[],[],[],[]]

incorrect_classifications = []

for train_indices,test_indices in kf.split(orig_text_sent):
    testingsen = []
    testingtag = []
    
    testingsen , testingtag = formRequiredTextTaggedList(orig_text_sent,orig_tagged_sent,test_indices)
    text_sent , tagged_sent = formRequiredTextTaggedList(orig_text_sent,orig_tagged_sent,train_indices)
    
    print('Length of test set is '+str(len(test_indices)))
    print('Length of train set is '+str(len(text_sent)))
    
    tag_dict = {}              # tag dictionary (Emision matrix)
    tag_count = {}             # count accurance of tags
    vocab ={}                  # vocabulary
    word_dict = {}             # word dictionary
    
    #forming word and tagdict
    for i in range(len(text_sent)):           
        for j in range(len(text_sent[i])):
            word, tag = text_sent[i][j] , tagged_sent[i][j]
            if word not in word_dict:
                word_dict[word] = {}
            if tag in word_dict[word]:
                word_dict[word][tag] += 1
            else:
                word_dict[word] = {tag:1}
            
            if tag in tag_dict:
                if word in tag_dict[tag]:
                    tag_dict[tag][word] += 1
                else:
                    tag_dict[tag][word] = 1
                tag_count[tag] += 1
#                 formVocabDict(word)
            else:
                tag_dict[tag] = {word:1}
                tag_count[tag] = 1
            if word in vocab:
                vocab[word] += 1
            else:
                vocab[word] = 1
#             updateTagAndWordDict(word,tag)
    
    #normalizing tag_dict
    for i in tag_dict:
        for j in tag_dict[i]:
            tag_dict[i][j] /= tag_count[i]
    
    #transition matrix
    transition_matrix = formTransitionMatrix(tag_count,tagged_sent)
    
    acctemp = []

    #connfusion matrix
    confusion_matrix = {}
    for tag in tag_count:
        confusion_matrix[tag] = {}
        for tag2 in tag_count:
            confusion_matrix[tag][tag2] = 0
    
    #tagwise precision matrix
    tagwise_metric = {}    
    for tag in tag_count:
        tagwise_metric[tag] = {"tp":0,"fp":0,"fn":0}
    
    
    errors = []
    
    # Testing start
    for test_text_ind in range(len(testingsen)):  
        test_text = testingsen[test_text_ind]
        que1 = []
        que2 = []

        for tag in transition_matrix["ST1"]:
            if  tag != "END1" and transition_matrix["ST1"][tag] * getEmissionProb(test_text[0],tag,tag_dict,vocab) > 0:
                que1.append([tag])
                que2.append(transition_matrix["ST1"][tag] )
        
        for tword_ind in range(1,len(test_text)):
            t1 = []
            t2 = []
            removlist = []

            while(que1):
                temp1 = que1.pop()
                temp2 = que2.pop()

                for tag in tag_count:
                    sss = transition_matrix[temp1[-1]][tag] * getEmissionProb(test_text[tword_ind],tag,tag_dict,vocab) * temp2
                    if  sss > 0:
                        t1.append(temp1 + [tag])
                        t2.append(sss)
                        removlist.append(sss)
            que1 = t1
            que2 = t2
#             remover()
            rem = 5                   # tune your speed lesser is higher
            if len(removlist) > rem:
                removlist.sort(reverse = True)
                ele = removlist[rem]
                for i in range(len(que2)-1,-1,-1):
                    if que2[i] < ele:
                        que1.pop(i)
                        que2.pop(i)
        
        incorrect = False
        incorrect_sample = {'tags':[]}
        try:
            anspos = que2.index(max(que2))
            accuracy = 0
            for ttag_ind in range(len(testingtag[test_text_ind])):
                if testingtag[test_text_ind][ttag_ind] == que1[anspos][ttag_ind]:
                    confusion_matrix[que1[anspos][ttag_ind]][que1[anspos][ttag_ind]] += 1
                    tagwise_metric[que1[anspos][ttag_ind]]["tp"] += 1
                    accuracy += 1
                else:
                    incorrect = True
                    incorrect_sample['tags'].append([ttag_ind,testingtag[test_text_ind][ttag_ind],que1[anspos][ttag_ind]])
                    confusion_matrix[testingtag[test_text_ind][ttag_ind]][que1[anspos][ttag_ind]] += 1
                    tagwise_metric[que1[anspos][ttag_ind]]["fp"] += 1
                    tagwise_metric[testingtag[test_text_ind][ttag_ind]]["fn"] += 1
            if incorrect:
                incorrect_sample['text'] = test_text
                incorrect_classifications.append(incorrect_sample)
            accuracy = (accuracy / len(testingtag[test_text_ind])) * 100
            acctemp.append(accuracy)
        except:
#             print('Here')
#             print(len(que1))
#             print(len(testingtag[test_text_ind]))
#             print()
#             acctemp.append(0)
            pass
        
    print('Accuracy for fold '+str(i)+ " is " +str(sum(acctemp)/len(acctemp)))
    
    folder_path = 'HMM_Fold'+str(foldi)
    try:
        os.mkdir(folder_path)
    except:
        # the folder is already created
        pass
       
    df = pd.DataFrame(confusion_matrix)
    df.to_csv(folder_path+"/confusionmatrixbi.csv")
    
    print("\n\nNumber of words for each tag :")
    for i in tag_dict:
        print(i,len(tag_dict[i]))

    tagfile = open(folder_path+'/noofwordsinTag.txt','wt')
    tagfile.write(str(tag_dict))
    tagfile.close()
    
    print("\n\nWords having more than 1 tag")
    for i in word_dict:
        if len(word_dict[i]) > 1:
            print(i , word_dict[i])
    
    average = [[],[],[]] 
    for i in tagwise_metric:
        tagwise_metric, average = precall(i,tagwise_metric,average)

    df = pd.DataFrame(tagwise_metric)
    df.to_csv(folder_path+"/tagwisebi.csv")
    
    print("\nAverage precision = ", sum(average[0])/len(average[0]))
    print("Average recall = ", sum(average[1])/len(average[1]))
    print("Average f1 Score = ", sum(average[2])/len(average[2]))
    
    total_metric[0].append(sum(acctemp)/len(acctemp))
    total_metric[1].append(sum(average[0])/len(average[0]))
    total_metric[2].append(sum(average[1])/len(average[1]))
    total_metric[3].append(sum(average[2])/len(average[2]))
    
    foldi+=1
#     break
    print("Total words present = ",len(vocab))
    print("Total tags present = ",len(tag_count))

    print("\nAverage accuracy = ", sum(acctemp)/len(acctemp))
#     print('Time: ', stop - start) 


with open('HMM_incorrect_classifications', 'w') as fout:
    json.dump(incorrect_classifications, fout)

print('\nOverall Statistics')
print('Final Accuracy = ',sum(total_metric[0])/len(total_metric[0]))
print('Final Precision = ',sum(total_metric[1])/len(total_metric[1]))
print('Final Recall = ',sum(total_metric[2])/len(total_metric[2]))
print('Final F1 Score = ',sum(total_metric[3])/len(total_metric[3]))

print("Total sentencess = ",  len(senten_length))
print("Maximum length sentences = ", max(senten_length))
print("Minimum length sentences = ",min(senten_length))
print("Average length of sentences= ", sum(senten_length)/len(senten_length))

Length of test set is 9164
Length of train set is 18327
Here
0
125

Here
0
146

Here
0
130

Here
0
265

Here
0
324

Here
0
271

Here
0
181

Here
0
121

Here
0
141

Here
0
386

Here
0
256

Here
0
171

Here
0
134

Here
0
144

Here
0
145

Here
0
141

Here
0
162

Here
0
118

Here
0
137

Here
0
130

Accuracy for fold 0 is 88.91218488299525


Number of words for each tag :
CONJ 23
ADV 1285
. 12
PRT 339
VERB 5766
NOUN 12137
ADP 180
DET 66
ADJ 3329
PRON 65
NUM 168
X 214

Average precision =  0.8811151364945772
Average recall =  0.8251926179085703
Average f1 Score =  0.8327366324137583
Length of test set is 9164
Length of train set is 18327
Here
0
172

Here
0
142

Accuracy for fold 0 is 93.47440389290813


Number of words for each tag :
ADP 197
DET 64
NOUN 15762
VERB 6655
ADJ 4737
CONJ 23
PRT 259
. 14
ADV 1464
NUM 765
PRON 56
X 314

Average precision =  0.9076125911877116
Average recall =  0.8687930995616283
Average f1 Score =  0.8779555159480158
Length of test set is 9163
Length of train set i

# Task 2 - MLP Classifier

In [1]:
# task 2, header files

from gensim.models import Word2Vec,KeyedVectors
from sklearn.neural_network import MLPClassifier
import numpy as np
import timeit

In [2]:
# word2vecmodel = KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin', binary=True)

In [2]:
start = timeit.default_timer()   # to note time
filename = "Brown_tagged_train.txt"

print("Reading the file..........\n")
f = open(filename, "r")
maintxt = f.read()
sentences = list(map(str,maintxt.split("\n")))
for i in range(len(sentences)-1,-1,-1):
    if len(sentences[i])< 2:
        sentences.pop(i)

Reading the file..........



In [3]:
print("Breaking into sentencess and tags..........\n")    

def breakWordTag(s):
    if s.find("/") > 0:
        l  = s.split("/")
        return " ".join(l[:-1]) , l[-1]
    return None,None

# tag_dict = {}              # tag dictionary (Emision matrix)
# tag_count = {}             # count accurance of tags
# vocab ={}                  # vocabulary
# word_dict = {}             # word dictionary

text_sent = []             # contain list of sentencess
tagged_sent = []           # contain list of ist of tagged sentencess

testingsen = []            # contain testing sentencess
testingtag = []            # contain testing tags

senten_length = []

for i in sentences:  
    ss = list(map(str,i.split()))       # process sentencess
    temp1 = []
    temp2 = []
    for j in ss:
        wor,tag = breakWordTag(j)
        if wor != None:
            temp1.append(wor)
            temp2.append(tag)
#             if wor not in word_dict:
#                 word_dict[wor] = {}
#             word_dict[wor][tag] = 0
    if len(temp1) > 1:                # remove lesser length sentencess
        text_sent.append(temp1)
        tagged_sent.append(temp2)
        senten_length.append(len(temp1))

orig_text_sent = text_sent
orig_tagged_sent = tagged_sent

Breaking into sentencess and tags..........



In [4]:
word2vecmodel = Word2Vec(text_sent,min_count=1,size=32)

In [9]:
X = []
Y = [] 
for i in range(10000):
    for j in range(len(text_sent[i])):
#         print(text_sent[i][j])
        try:
            X.append(word2vecmodel.wv[text_sent[i][j].split(" ")[0]])
        except:
            X.append(np.zeros(32).astype(float))
        Y.append(tagged_sent[i][j])

32

In [10]:
model = MLPClassifier(hidden_layer_sizes=(150,100,50), max_iter=300,activation = 'relu',solver='adam',random_state=1)

In [11]:
model.fit(X,Y)

/home/hokagehimanshu/.local/lib/python3.6/site-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)


ValueError: Expected 2D array, got 1D array instead:
array=[list(['At', 'that', 'time', 'highway', 'engineers', 'traveled', 'rough', 'and', 'dirty', 'roads', 'to', 'accomplish', 'their', 'duties', '.'])
 list(['Using', 'privately-owned', 'vehicles', 'was', 'a', 'personal', 'hardship', 'for', 'such', 'employees', ',', 'and', 'the', 'matter', 'of', 'providing', 'state', 'transportation', 'was', 'felt', 'perfectly', 'justifiable', '.'])
 list(['Once', 'the', 'principle', 'was', 'established', ',', 'the', 'increase', 'in', 'state-owned', 'vehicles', 'came', 'rapidly', '.'])
 ...
 list(['Compassionately', 'yours', ',', 'S.', 'J.', 'Perelman', 'revulsion', 'in', 'the', 'desert', 'the', 'doors', 'of', 'the', 'D', 'train', 'slid', 'shut', ',', 'and', 'as', 'I', 'dropped', 'into', 'a', 'seat', 'and', ',', 'exhaling', ',', 'looked', 'up', 'across', 'the', 'aisle', ',', 'the', 'whole', 'aviary', 'in', 'my', 'head', 'burst', 'into', 'song', '.'])
 list(['She', 'was', 'a', 'living', 'doll', 'and', 

At
that
time
highway
engineers
traveled
rough
and
dirty
roads
to
accomplish
their
duties
.
Using
privately-owned
vehicles
was
a
personal
hardship
for
such
employees
,
and
the
matter
of
providing
state
transportation
was
felt
perfectly
justifiable
.
Once
the
principle
was
established
,
the
increase
in
state-owned
vehicles
came
rapidly
.
And
reasons
other
than
employee
need
contributed
to
the
growth
.
Table
1
immediately
below
shows
the
rate
of
growth
of
vehicles
and
employees
.
This
rate
of
increase
does
not
signify
anything
in
itself
.
It
does
not
indicate
loose
management
,
ineffective
controls
or
poor
policy
.
But
it
does
show
that
automobiles
have
increased
steadily
over
the
years
and
in
almost
the
same
proportion
to
the
increase
of
state
employees
.
In
the
past
twenty
years
the
ratio
of
state-owned
automobiles
per
state
employees
has
varied
from
1
to
22
then
to
1
to
23
now
.
Whether
there
were
too
few
automobiles
in
1940
or
too
many
now
is
problematical
.
The
fact
is
simply
that
st

the
assessors
are
of
significance
in
indicating
what
their
thinking
seems
to
be
at
the
present
time
.
In
reply
to
a
question
of
whether
they
now
tax
boats
,
airplanes
and
other
movable
property
excluding
automobiles
,
nineteen
said
that
they
did
and
twenty
that
they
did
not
.
The
wording
of
the
question
was
quite
general
and
may
have
been
subject
to
different
interpretations
.
One
assessor
checked
boats
only
,
another
trailers
and
tractors
,
one
mentioned
house
trailers
,
and
two
others
referred
to
trailers
without
specifying
the
type
.
In
two
cases
,
airplanes
only
were
indicated
.
It
is
difficult
to
tabulate
exactly
what
was
meant
in
each
individual
situation
,
but
the
conclusion
may
be
drawn
that
21
towns
do
not
assess
movable
personal
property
,
and
of
the
remainder
only
certain
types
are
valued
for
tax
purposes
.
Boats
were
indicated
specifically
by
only
one
of
the
five
towns
known
to
tax
boats
.
It
would
seem
,
then
,
that
movable
property
and
equipment
is
not
taxed
as
a
whole
bu

Institute
of
Public
Administration
that
``
Metropolian
Planning
(
in
Rhode
Island
)
means
,
or
should
mean
,
state
planning
''
,
the
state
guide
plan
will
take
into
account
the
metropolitan
nature
of
many
of
Rhode
Island's
problems
.
(
3
)
It
will
continue
to
be
an
objective
of
this
division
to
encourage
the
acceptance
of
planning
as
a
proper
and
continuing
responsibility
of
local
government
.
To
this
end
,
the
community
assistance
program
of
the
planning
division
will
continue
to
be
operated
as
a
staff
function
to
make
available
,
on
a
shared
cost
basis
,
technical
planning
assistance
to
those
communities
in
the
state
unable
to
maintain
their
own
planning
staff
.
(
4
)
The
planning
division
will
take
the
initiative
in
encouraging
planning
cooperation
at
all
levels
of
government
;
;
among
the
operating
departments
of
the
state
;
;
between
the
cities
and
towns
of
the
state
;
;
and
on
a
regional
basis
between
the
six
New
England
states
.
(
5
)
On
the
basis
that
all
citizens
of
the
state


nine
months
,
commencing
with
September
30
and
ending
with
June
30
.
These
three
installment
dates
would
be
:
October
26
,
January
26
,
and
April
25
(
Providence
)
and
November
15
,
February
16
and
May
15
(
Cranston
)
.
Both
would
start
their
new
fiscal
year
on
July
1
.
Their
tax
collection
calendar
could
then
be
:
July
25
,
October
26
,
January
26
,
and
April
25
,
(
Providence
)
;
;
and
August
15
,
November
15
,
February
17
,
and
May
15
,
(
Cranston
)
.
Under
this
plan
both
Cranston
and
Providence
would
be
on
the
uniform
fiscal
year
but
would
still
be
using
the
same
installment
periods
.
Varying
adjustments
.
The
remaining
twenty-three
towns
have
fiscal
years
which
end
prior
to
June
30
.
All
of
these
towns
will
require
adjustments
of
both
their
fiscal
and
tax
collection
years
.
Assuming
an
adjustment
to
the
July
1
to
June
30
fiscal
year
,
the
required
adjustment
of
the
tax
collection
years
and
the
towns
involved
are
shown
in
Table
3
.
Methods
of
financing
adjustments
Aside
from
the
ma

the
Nation
and
the
importance
of
finding
new
sources
of
supply
to
meet
its
present
and
future
water
needs
,
it
is
the
policy
of
the
Congress
to
provide
for
the
development
of
practicable
low-cost
means
for
the
large-scale
production
of
water
of
a
quality
suitable
for
municipal
,
industrial
,
agricultural
,
and
other
beneficial
consumptive
uses
from
saline
water
,
and
for
studies
and
research
related
thereto
.
As
used
in
this
Act
,
the
term
'
saline
water
'
includes
sea
water
,
brackish
water
,
and
other
mineralized
or
chemically
charged
water
,
and
the
term
'
United
States
'
extends
to
and
includes
the
District
of
Columbia
,
the
Commonwealth
of
Puerto
Rico
,
and
the
territories
and
possessions
of
the
United
States
.
Sec.
2
.
In
order
to
accomplish
the
purposes
of
this
Act
,
the
Secretary
of
the
Interior
shall
--
(
A
)
conduct
,
encourage
,
and
promote
fundamental
scientific
research
and
basic
studies
to
develop
the
best
and
most
economical
processes
and
methods
for
converting
saline
wa

...

The
misplaced
modifier
is
another
species
more
honored
in
the
observance
of
obscurity
than
in
the
breach
.
This
creates
an
amusing
effect
because
its
position
in
a
sentence
seems
to
make
it
apply
to
the
wrong
word
.
A
verse
familiar
to
all
grammarians
is
the
quatrain
:
``
I
saw
a
man
once
beat
his
wife
When
on
a
drunken
spree
.
Now
can
you
tell
me
who
was
drunk
--
The
man
,
his
wife
,
or
me
''
?
The
``
wooden-leg
''
gag
of
vaudeville
,
another
standby
of
this
sort
,
had
endless
variations
.
``
There's
a
man
outside
with
a
wooden
leg
named
Smith
''
.
``
What's
the
name
of
his
other
leg
''
?
Another
stock
vaudeville
gag
ran
:
``
Mother
is
home
sick
in
bed
with
the
doctor
''
.
When
radio
came
in
,
it
continued
the
misplaced
modifier
in
its
routines
as
a
standard
device
.
``
Do
you
see
that
pretty
girl
standing
next
to
the
car
with
slacks
on
''
?
``
I
see
the
girl
but
I
don't
see
the
car
with
slacks
on
''
.
In
recent
years
gagwriters
have
discovered
this
brand
of
blunder
and
thus
the
mispl

.
``
I'll
try
''
,
I
said
,
and
sat
for
a
moment
thinking
.
``
Oh
yes
,
the
other
day
I
reread
some
of
Emerson's
English
Traits
,
and
there
was
an
anecdote
about
a
group
of
English
and
Americans
visiting
Germany
,
more
than
a
hundred
years
ago
.
In
the
railway
station
at
Berlin
,
a
uniformed
attendant
was
chanting
,
'
Foreigners
this
way
!
Foreigners
this
way
'
!
One
woman
--
she
could
have
been
either
English
or
American
--
went
up
to
him
and
said
,
'
But
you
are
the
foreigners
'
''
.
I
took
a
deep
breath
and
an
even
deeper
swallow
of
my
drink
,
and
said
,
``
I
admit
that
going
back
to
Ralph
Waldo
Emerson
for
humor
is
like
going
to
a
modern
musical
comedy
for
music
and
comedy
''
.
``
What's
the
matter
with
the
music
''
?
Moreland
asked
.
``
It
doesn't
drown
out
the
dialogue
''
,
I
explained
.
``
Let's
talk
about
books
''
,
Moreland
said
.
``
I
am
told
that
in
America
you
have
non-books
by
non-writers
,
brought
out
by
non-publishers
for
non-readers
.
Is
it
all
non-fiction
''
?
``
There

whose
reflexes
and
replies
were
invariably
so
admirably
normal
and
predictable
.
Maybe
that
was
why
they
were
cordial
and
loyal
towards
the
unpredictability
of
Arlene
.
``
Just
you
wait
''
,
advised
Arlene
,
echoing
the
dialogue
in
a
recent
British
movie
.
And
when
they
had
got
to
their
little
lawn
,
they
had
had
a
most
twirlingly
magnificent
time
.
First
,
Arlene
had
put
them
through
some
rapid
somersaults
.
They
had
protested
that
that
wasn't
any
surprise
.
``
Just
you
wait
''
,
said
Arlene
again
,
as
though
she
were
discovering
the
pleasantly
tingling
insinuations
of
that
handy
little
sturdy
statement
.
``
This
is
a
warm-up
''
.
``
Is
it
anything
like
cooked-over
oatmeal
''
?
Asked
one
of
the
children
.
``
Not
the
least
bit
''
,
Arlene
snapped
.
One
of
the
many
things
that
was
so
nice
about
her
was
that
she
always
took
your
questions
seriously
,
particularly
your
very
,
very
serious
questions
.
Those
were
especially
the
ones
that
all
other
grownups
laughed
at
loudest
.
She
would
som

cults
.
It's
somewhat
off
the
beaten
track
,
to
be
sure
,
but
therein
lies
its
variety
and
charm
.
For
example
,
probably
very
few
people
know
that
the
word
``
visrhanik
''
that
is
bantered
about
so
much
today
stems
from
the
verb
``
bouanahsha
''
:
to
salivate
.
Likewise
,
and
equally
fascinating
,
is
the
news
that
such
unlikely
synonyms
as
``
pratakku
''
,
``
sweathruna
''
,
and
the
tongue-twister
``
nnuolapertar-it-vuh-karti-birifw-
''
all
originated
in
the
same
village
in
Bathar-on-Walli
Province
and
are
all
used
to
express
sentiments
concerning
British
``
imperialism
''
.
The
terms
are
fairly
safe
to
use
on
this
side
of
the
ocean
,
but
before
you
start
spouting
them
to
your
date
,
it
might
be
best
to
find
out
if
he
was
a
member
of
Major
Pockmanster's
Delhi
Regiment
,
since
resentment
toward
the
natives
was
reportedly
very
high
in
that
outfit
.
The
breeze
and
chancellor
Neitzbohr
,
a
movie
melodrama
that
concerns
the
attempts
of
a
West
German
politician
to
woo
a
plaster
cast
of
the


two
snuffboxes
,
and
a
jade-handled
magnifying
glass
.
Rummaging
through
a
stack
of
drawers
nearby
,
you
unearthed
an
antique
French
chess
set
in
ivory
and
sandalwood
,
which
,
along
with
two
box
Kodaks
,
you
added
to
your
haul
.
Then
,
having
wrapped
the
lot
in
an
afghan
my
dog
customarily
slept
on
,
you
lammed
out
the
front
door
,
considerately
leaving
it
open
for
neighbors
to
discover
.
So
much
for
the
tiresome
facts
,
as
familiar
to
you
,
I'm
sure
,
as
to
the
constables
and
state
troopers
who
followed
in
your
wake
.
The
foregoing
,
aided
by
several
clues
I'll
withhold
to
keep
you
on
your
toes
,
will
pursue
you
with
a
tenacity
worthy
of
Inspector
Javert
,
but
before
they
close
in
,
gird
yourselves
,
I
repeat
,
for
a
vengeance
infinitely
more
pitiless
.
Fourteen
of
the
sculptures
you
took
possess
properties
of
a
most
curious
and
terrifying
nature
,
as
you
will
observe
when
your
limbs
begin
to
wither
and
your
hair
falls
out
in
patches
.
In
time
,
these
minor
manifestations
will
multip

NameError: name 'float32' is not defined

543126

In [ ]:
model.fit(X,Y)

In [66]:
# # It is not feasible to run trigram in notebook because it takes 10 - 20 GB of data 
# # I ran trigram on iiit Delhi server which has 50 GB of RAM and 20 cores of CPU


# transition_matrixtri = {str(["ST1","ST2"]):{}}   # making of transition matrix for trigram
# for i in tag_count:
# 	transition_matrixtri[str(["ST2",i])] = {}

# for i in tag_count:
# 	for j in tag_count:
# 		transition_matrixtri[str([i,j])] = {}

# for i in transition_matrixtri:
# 	for j in tag_count:
# 		transition_matrixtri[i][j] = 1                     # SMOOTHING

# for i in tagged_sent:
# 	try:
# 		transition_matrixtri[str(["ST1","ST2"])][i[0]] += 1
# 		transition_matrixtri[str(["ST2",i[0]])][i[1]] += 1
# 	except:
# 		print(i)

# for i in tagged_sent:
# 	for j in range(2,len(i)):
# 		transition_matrixtri[str([i[j-2],i[j-1]])][i[j]] += 1

# for i in transition_matrixtri:
# 	coun = 0
# 	for j in transition_matrixtri[i]:
# 		coun += transition_matrixtri[i][j]

# 	coun = max(1,coun)
# 	for j in transition_matrixtri[i]:
# 		transition_matrixtri[i][j] /= coun



In [ ]:
# start = timeit.default_timer()
# acctemp = []


# confusion_matrix = {}          # confusion matrix for trigrams
# for i in tag_count:
# 	confusion_matrix[i] = {}
# 	for j in tag_count:
# 		confusion_matrix[i][j] = 0

# tagwise_metric = {}        # tagwise precision,recall for trigrams
# for i in tag_count:
# 	tagwise_metric[i] = {"tp":0,"fp":0,"fn":0}

In [ ]:
# print("Testing start .........")
# for test in range(len(testingsen)):         # test data to be trained
# 	test_text = testingsen[test] 
	
# 	que1 = []
# 	que2 = []

# 	for i in transition_matrixtri[str(["ST1","ST2"])]:
# 		if  i != "END1" and transition_matrixtri[str(["ST1","ST2"])][i] * getEmissionProb(test_text[0],i) > 0:
# 			que1.append([i])
# 			que2.append(transition_matrixtri[str(["ST1","ST2"])][i])

# 	for i in range(1,len(test_text)):
# 		t1 = []
# 		t2 = []
# 		removlist = []

# 		while(que1):
# 			temp1 = que1.pop()
# 			temp2 = que2.pop()
# 			if len(temp1) == 1:
# 				for j in tag_count:
# 					sss = transition_matrixtri[str(["ST2",temp1[-1]])][j] * getEmissionProb(test_text[i],j) * temp2
# 					if  sss > 0:
# 						t1.append(temp1 + [j])
# 						t2.append(sss)
# 						removlist.append(sss)
# 			else:
# 				for j in tag_count:
# 					sss = transition_matrixtri[str([temp1[-2],temp1[-1]])][j] * getEmissionProb(test_text[i],j) * temp2
# 					if  sss > 0:
# 						t1.append(temp1 + [j])
# 						t2.append(sss)
# 						removlist.append(sss)


# 		que1 = t1
# 		que2 = t2

# 		remover()

# 	try:           # try catch to handle errors SMOOTHING
# 		anspos = que2.index(max(que2))
# 		accuracy = 0
# 		for i in range(len(testingtag[test])):
# 			if testingtag[test][i] == que1[anspos][i]:
# 				confusion_matrix[que1[anspos][i]][que1[anspos][i]] += 1
# 				tagwise_metric[que1[anspos][i]]["tp"] += 1
# 				accuracy += 1
# 			else:
# 				confusion_matrix[testingtag[test][i]][que1[anspos][i]] += 1
# 				tagwise_metric[que1[anspos][i]]["fp"] += 1
# 				tagwise_metric[testingtag[test][i]]["fn"] += 1

# 		accuracy = accuracy / len(testingtag[test]) * 100
# 		print(test+1,"Accuracy =",accuracy,"%")
# 		acctemp.append(accuracy)

# 	except:
# 		pass


# 	#print("\n\n\n")



In [ ]:
# average = [[],[],[]]      # contain average for precion,recall, F1-score
# def precall(ke): 
# 	fn = tagwise_metric[ke]["fn"]
# 	fp = tagwise_metric[ke]["fp"]
# 	tp = tagwise_metric[ke]["tp"]
# 	try:
# 		precision = tp/(tp+fp)
# 		recall = tp/(tp+fn)
# 		f1s = 2/((1/recall)+(1/precision))
# 		average[0].append(precision)
# 		average[1].append(recall)
# 		average[2].append(f1s)
# 	except:
# 		precision = 0
# 		recall = 0
# 		f1s = 0	
	
# 	tagwise_metric[ke]["precision"] = precision
# 	tagwise_metric[ke]["recall"] = recall
# 	tagwise_metric[ke]["f1s"] = f1s


# 	#print("\n\n\n")

# df = pd.DataFrame(confusion_matrix)
# df.to_csv("confusionmatrixtri.csv")




# print("\n\nNumber of words for each tag :")
# for i in tag_dict:
# 	print(i,len(tag_dict[i]))

# print("\n\nWords having more than 1 tag")
# for i in word_dict:
# 	if len(word_dict[i]) > 1:
# 		print(i , word_dict[i])

# for i in tagwise_metric:
# 	precall(i)

# df = pd.DataFrame(tagwise_metric)
# df.to_csv("tagwisetri.csv")

# print("\nAverage precision = ", sum(average[0])/len(average[0]))
# print("Average recall = ", sum(average[1])/len(average[1]))
# print("Average f1 Score = ", sum(average[2])/len(average[2]))

# print("Total words present = ",len(vocab))
# print("Total tags present = ",len(tag_count))
# print("Total sentencess = ",  len(senten_length))
# print("Maximum length sentences = ", max(senten_length))
# print("Minimum length sentences = ",min(senten_length))
# print("Average length of sentences= ", sum(senten_length)/len(senten_length))

# stop = timeit.default_timer()

# print("\nAverage accuracy = ", sum(acctemp)/len(acctemp))
# print('Time: ', stop - start) 
